<a href="https://colab.research.google.com/github/sreeman-11021996/Fashion-Recommendation-system/blob/main/resnet_transfer_image_feature_extractor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [16]:
!pip install tensorflow-gpu

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [15]:
!nvidia-smi

NVIDIA-SMI has failed because it couldn't communicate with the NVIDIA driver. Make sure that the latest NVIDIA driver is installed and running.



In [4]:
!pip install import_ipynb
import import_ipynb

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.6 MB 4.2 MB/s 


In [5]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/

In [6]:
!kaggle datasets download -d paramaggarwal/fashion-product-images-small

100% 565M/565M [00:19<00:00, 33.6MB/s]
100% 565M/565M [00:19<00:00, 30.8MB/s]


In [7]:
import zipfile
zip_ref = zipfile.ZipFile("/content/fashion-product-images-small.zip", "r")
zip_ref.extractall("/content")
zip_ref.close()

In [8]:
import tensorflow
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.resnet50 import preprocess_input
from tensorflow.keras.layers import GlobalMaxPooling2D
from keras.models import model_from_json,Sequential

import pandas as pd
import numpy as np
from numpy.linalg import norm
import os
from tqdm import tqdm
import pickle

In [9]:
# get data

In [10]:
# get the model

In [11]:
file = open("/content/myModel_arc_transfer.json")
loaded_model = file.read()
file.close()

In [12]:
loaded_model_final = model_from_json(loaded_model)
loaded_model_final.load_weights("/content/myModel_wts_transfer.h5")

OSError: ignored

In [10]:
loaded_model_final.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 resnet50 (Functional)       (None, 7, 7, 2048)        23587712  
                                                                 
 global_max_pooling2d (Globa  (None, 2048)             0         
 lMaxPooling2D)                                                  
                                                                 
 fc56 (Dense)                (None, 56)                114744    
                                                                 
Total params: 23,702,456
Trainable params: 15,090,744
Non-trainable params: 8,611,712
_________________________________________________________________


In [16]:
model = Sequential()
model.add(loaded_model_final.layers[0])
model.add(loaded_model_final.layers[1])

In [20]:
model.trainable=False

In [22]:
model.compile(optimizer="adam",loss="categorical_crossentropy",metrics=["accuracy"])

In [23]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 resnet50 (Functional)       (None, 7, 7, 2048)        23587712  
                                                                 
 global_max_pooling2d (Globa  (None, 2048)             0         
 lMaxPooling2D)                                                  
                                                                 
Total params: 23,587,712
Trainable params: 0
Non-trainable params: 23,587,712
_________________________________________________________________


In [24]:
def extract_features(img_path,model):
    # load the image
    img = image.load_img(img_path,target_size=(224,224))
    # img -> array
    img_array = image.img_to_array(img)
    # keras only takes images in batches
    expanded_img_array = np.expand_dims(img_array,axis=0)
    # preprocess img according to ResNet50
    processed_img = preprocess_input(expanded_img_array)
    # extract the features
    result = model.predict(processed_img).flatten()
    # l2 norm.
    normalized_result = result/norm(result)
    
    return normalized_result

In [25]:
filenames = []

for file in os.listdir("/content/images"):
    if file not in [".ipynb_checkpoints"]:
        filenames.append(os.path.join("images",file))

In [26]:
len(filenames)

44441

In [ ]:
feature_list = []

for file in tqdm(filenames):
    feature_list.append(extract_features(file,model))

  0%|          | 0/44441 [00:00<?, ?it/s]

1/1 [==============================] - 8s 8s/step


  0%|          | 1/44441 [00:11<136:54:23, 11.09s/it]

1/1 [==============================] - 0s 22ms/step


  0%|          | 3/44441 [00:11<36:07:23,  2.93s/it] 

...

1/1 [==============================] - 0s 35ms/step


 43%|████▎     | 19152/44441 [31:05<46:30,  9.06it/s]

1/1 [==============================] - 0s 34ms/step


 43%|████▎     | 19154/44441 [31:05<42:14,  9.98it/s]

1/1 [==============================] - ETA: 0s

In [ ]:
pickle.dump(feature_list,open('embeddings.pkl','wb'))
pickle.dump(filenames,open('filenames.pkl','wb'))